In [4]:
!pip install plotly

In [7]:
import pandas as pd
import numpy as np
import seaborn as sns
import tqdm
import matplotlib.pyplot as plt
import plotly.express as px
import itertools
import math
import random

# BDI model
## Belief:
- Compliance of other agents
- Estimated health status of neighbors
- Regulation strictness 
## Desire:
- Remain healthy and avoid infection
- Minimise effort (avoid compliance and wear mask...)
- Social desires (compling because other are)
## Intention:
- Whether to comply
- Whether to free ride

# Orders:
## Oth order:
- Belief: basic enviromental factors (`default_strategy`)
- Desire: stay safe and minimise effort
- Intention: Decide whether to comply without considering others
## 1st order:
- Belief: everything in 0th + other agents' likely compliance
- Desire: everything in 0th + other agents' actions influence how desires are prioritised.
- Intentions: everything in 0th + belif over other agent behaviour affects intention. For example if most comply then free-riding looks inviting
$$ P(W
## 2nd order:
- Belief: everything in 1st + recusive understanding of other's behaviour
- Desire: everything in 1st + desire to ancicipate and leverage other's behaviour
- Intention: everything in 1st but more in depth

In [3]:
# I is % infected agents
# H is health-status (0 if infected or immune, 1 if healthy)
# R is Regulation Strictness
# C is willingness to comply

def default_strategy(I, R, C, H):
    if H == 1:
        p = 0.34*I + 0.33*(R * (100 - C)/100) + 0.33*C
    elif H == 0:
        p = 0.34*(-I) + 0.33*(R * (100 - C)/100) + 0.33*C
    elif H == 2:
        p = 0.5*(R * (100 - C)/100) + 0.5*C
    normalized_p = (p + 100) / 200  # Shift and scale
    return normalized_p

In [4]:
I = 30
R = 70
H = 0
C = 50

print(default_strategy(I,R,C,H))

0.5892499999999999


# Mathematical Explanation of Theory of Mind Compliance Strategies

In this explanation, we explore the **0th-order**, **1st-order**, and **2nd-order Theory of Mind (ToM)** compliance strategies for agents, focusing on their progressively deeper reasoning about the environment, their desires, and their beliefs regarding other agents.

## 0th-Order Theory of Mind: Default Strategy

The **0th-order ToM** agent uses a **default strategy** that depends solely on **environmental factors** such as infection rate, regulation strictness, compliance rate, and health status. These agents do **not** consider the actions or beliefs of other agents.

### Default Strategy Function
The provided function for **0th-order ToM** is:

$$
\text{default\_strategy}(I, R, C, H) = 
\begin{cases}
    0.34 \times I + 0.33 \times \left( R \times \frac{100 - C}{100} \right) + 0.33 \times C & \text{if } H = 1 \text{ (Healthy)} \\
    0.34 \times (-I) + 0.33 \times \left( R \times \frac{100 - C}{100} \right) + 0.33 \times C & \text{if } H = 0 \text{ (Infected)} \\
    0.5 \times \left( R \times \frac{100 - C}{100} \right) + 0.5 \times C & \text{if } H = 2 \text{ (Immune)}
\end{cases}
$$

Where:
- **$( I )$**: Infection Rate ($(0 \leq I \leq 1)$)
- **$( R )$**: Regulation Strictness ($(0 \leq R \leq 1)$)
- **$( C )$**: Compliance rate by others (as a percentage, $(0 \leq C \leq 100)$)
- **$( H )$**: Health Status ($(1)$ for **Healthy**, $(0)$ for **Infected**, $(2)$ for **Immune**)

The **default strategy** is then **normalized** to bring the compliance probability between 0 and 1:

```math
\text{normalized\_p} = \frac{p + 100}{200}
```

### Explanation
- **Healthy Agents ($(H = 1)$)**: Positive influence of **infection rate** ($(I)$) encourages compliance. **Regulation strictness** ($(R)$) and existing **compliance rate** ($(C)$) also influence the decision.
- **Infected Agents ($(H = 0)$)**: Infected agents are less influenced by infection rate ($(-I)$) as they are already infected. **Regulation strictness** and others' **compliance** encourage them to comply to avoid spreading the virus.
- **Immune Agents ($(H = 2)$)**: Immune agents have less motivation to comply due to personal risk, so the influence is more evenly split between regulation strictness and compliance.

## 1st-Order Theory of Mind: Considering Compliance of Others

The **1st-order ToM** agent builds upon the **0th-order** by adding consideration of **what others are doing**. This includes a belief about the **perceived compliance of other agents ($(C_O)$)**.

### Mathematical Model
The **compliance probability** for a **1st-order ToM** agent is given by:

$$
P(W = 1 | I, R, C, H, C_O) = \frac{1}{1 + e^{-(\beta_0 + \beta_1 I + \beta_2 R + \beta_3 H + \beta_4 C + \gamma_1 D_H - \gamma_2 D_E + \gamma_3 D_S)}}
$$

Where:
- **$( $beta_0$ )$**: Bias term, representing a baseline level of compliance.
- **$( $beta_1, beta_2, beta_3, beta_4$ )$**: Coefficients representing influences of **infection rate**, **regulation strictness**, **health status**, and **compliance rate**.
- **$( $gamma_1, gamma_2, gamma_3$ )$**: Coefficients for the agent's **desires**.

**Desires**:
1. **Desire to Remain Healthy ($(D_H$))**:
   - Calculated based on **infection rate $(I)$** and **health status ($(H)$)**.
   - Mathematically:

   $$
   D_H = \alpha_1 \times I + \alpha_2 \times (1 - H)
   $$

2. **Desire to Minimize Effort ($(D_E)$)**:
   - Represents the desire to avoid compliance effort. This is higher when regulations are lax, or others are already complying.
   - Mathematically:

   $$
   D_E = \alpha_3 \times (1 - R) + \alpha_4 \times (1 - C)
   $$

3. **Social Desire ($(D_S)$)**:
   - Agents want to comply if others comply. It depends directly on **perceived compliance by others ($(C_O)$)**.
   - Mathematically:

   $$
   D_S = \alpha_5 \times C_O
   $$

### Explanation
- The **logistic function** calculates the probability of compliance, incorporating the influence of both **environmental factors** and the **agent's internal desires**.
- The **1st-order ToM** agent is influenced not only by the environment but also by **how others are behaving**.
- If **others are complying** (high $(C_O)$), the **social desire ($(D_S)$)** increases, making the agent more likely to comply.

## 2nd-Order Theory of Mind: Considering Beliefs About Self

The **2nd-order ToM** agent extends the 1st-order by considering not only **what others are doing** but also **what others think about it**. This introduces a recursive level of reasoning, where agents make decisions based on **perceived beliefs about themselves**.

### Mathematical Model
The **compliance probability** for a **2nd-order ToM** agent is given by:

$$
P(W = 1 | I, R, C, H, C_O, B_S) = \frac{1}{1 + e^{-(\beta_0 + \beta_1 I + \beta_2 R + \beta_3 H + \beta_4 C + \gamma_1 D_H - \gamma_2 D_E + \gamma_3 D_S + \gamma_4 D_B)}}
$$

Where:
- **$( B_S )$**: Represents the **perceived beliefs about self**, i.e., what the agent believes that others believe about its behavior.
- **$( \gamma_4 )$**: Coefficient representing the influence of **desire influenced by others' beliefs ($(D_B)$)**.

**New Desire Introduced**:
1. **Desire Based on Beliefs About Self ($(D_B)$)**:
   - This desire models how agents change their behavior based on what they **think others believe** about them.
   - Mathematically:

   $$
   D_B = \gamma_4 \times B_S
   $$

### Explanation
- The **2nd-order ToM** agent attempts to **anticipate the beliefs of others** about its own compliance.
- **Beliefs about self ($(B_S)$)** influence compliance because the agent wants to manage **how it is perceived**.
- This **recursive reasoning** makes the agent capable of **more complex social strategies**, such as complying to maintain a positive perception, even if it otherwise would not comply.

## Summary of Mathematical Differences

1. **0th-Order ToM**:
   - Uses a default strategy relying solely on environmental factors:
   
   $$
   \text{default\_strategy}(I, R, C, H)
   $$
   
   - Normalized compliance probability using simple additive factors.

2. **1st-Order ToM**:
   - Incorporates **perceived compliance by others ($(C_O)$)** into the decision-making.
   - Uses a **logistic model** to compute compliance probability:

   $$
   P(W = 1) = \frac{1}{1 + e^{-(\text{environmental factors + desires})}}
   $$

   - Desires are included: **remain healthy**, **minimize effort**, **social desire**.

3. **2nd-Order ToM**:
   - Incorporates **beliefs about self ($(B_S)$)** in addition to **perceived compliance by others ($(C_O)$)**.
   - Uses a more complex logistic model to compute compliance probability:

   $$
   P(W = 1) = \frac{1}{1 + e^{-(\text{environmental factors + desires + beliefs about self})}}
   $$

   - Adds the **desire based on others' beliefs about itself**.

## Key Insights
- **0th-order ToM** agents are **reactive** and lack awareness of other agents.
- **1st-order ToM** agents are **socially aware** and adjust their actions based on what they **see others doing**.
- **2nd-order ToM** agents are **strategically aware** and take into account how **others perceive their behavior**, thus making more nuanced social decisions.

These models progressively add layers of social reasoning, enabling a richer understanding of complex group dynamics, which is crucial for simulating scenarios like **pandemic guideline compliance**, where compliance depends not only on individual risk assessment but also on social influences and perceptions.

In [8]:
#WEIGHTS
alpha1, alpha2, alpha3, alpha4, alpha5 = 0.7, 0.3, 0.5, 0.5, 0.9
gamma_1, gamma_2, gamma_3, gamma_4 = 1.0, 1.5, 0.8, 0.6

In [38]:
def first_order_strategy(I, R, C, H, perceived_compliance_others):

    #Desire to remail healty
    D_H = alpha1 * I + alpha2 * (1 - H)
    #Desire to Minimise effort
    D_E = alpha3 * (1 - R) + alpha4 * (1 - C)
    #Desire to be social
    D_S = alpha5 * perceived_compliance_others

    exponent = -(0.2 + 1.2 * I + 1.0 * R + 0.8 * H + 0.5 * C + gamma_1 * D_H - gamma_2 * D_E + gamma_3 * D_S)
    return 1 / (1 + math.exp(exponent))

# 2nd-order ToM: Adds Recursive Reasoning About Others' Beliefs
def second_order_strategy(I, R, C, H, perceived_compliance_others, perceived_beliefs_about_self):

    #Desire to remail healty
    D_H = alpha1 * I + alpha2 * (1 - H)
    #Desire to Minimise effort
    D_E = alpha3 * (1 - R) + alpha4 * (1 - C)
    #Desire to be social
    D_S = alpha5 * perceived_compliance_others
    D_B = gamma_4 * perceived_beliefs_about_self  # Desire influenced by how others think about itself

    exponent = -(0.2 + 1.2 * I + 1.0 * R + 0.8 * H + 0.5 * C + gamma_1 * D_H - gamma_2 * D_E + gamma_3 * D_S + D_B)
    return 1 / (1 + math.exp(exponent))

# Example usage of the strategies for agents at different ToM levels
def decide_compliance(agent, I, R, C, ToM_level, perceived_compliance_others=None, perceived_beliefs_about_self=None):
    H = agent["health_status"]

    if ToM_level == 0:
        compliance_prob = default_strategy(I, R, C, H)

    elif ToM_level == 1:
        if perceived_compliance_others is None:
            raise ValueError("1st-order ToM requires perceived_compliance_others.")
        compliance_prob = first_order_strategy(I, R, C, H, perceived_compliance_others)

    elif ToM_level == 2:
        if perceived_compliance_others is None or perceived_beliefs_about_self is None:
            raise ValueError("2nd-order ToM requires both perceived_compliance_others and perceived_beliefs_about_self.")
        compliance_prob = second_order_strategy(I, R, C, H, perceived_compliance_others, perceived_beliefs_about_self)

    return random.random() < compliance_prob, compliance_prob

In [10]:
###Example usage

agent = {"health_status": 1}  # Healthy agent
infection_rate = 0.3
regulation_strictness = 0.3
compliance_by_others = 0.4

compliance_decision, compliance_probability = decide_compliance(agent, infection_rate, regulation_strictness, compliance_by_others, 2, 0.6, 0.5)
print("Agent complies:", compliance_decision)
print(f'With probability {compliance_probability}')

Agent complies: True
With probability 0.8614039534506838


In [44]:
import numpy as np
import pandas as pd
import plotly.express as px
import random

# Step 1: Generate a reduced set of environmental variables with coarser steps
health_statuses = [0]  # 0: Infected, 1: Healthy, 2: Immune
infection_rates = np.linspace(0, 1, 3)  # Reduced steps: [0, 0.5, 1]
regulation_strictness = np.linspace(0, 1, 3)  # Reduced steps: [0, 0.5, 1]
compliance_by_others = np.linspace(0, 1, 3)  # Reduced steps: [0, 0.5, 1]

# Step 2: Define ranges for the parameters with reduced step size
alpha_values = np.linspace(0, 1, 3)  # Reduced steps for alpha values: [0.1, 1.05, 2.0]
gamma_values = np.linspace(0, 1, 3)  # Reduced steps for gamma values: [0.1, 1.05, 2.0]

# Step 3: Create a sample of combinations
# Create all possible combinations of environmental variables and parameters
all_combinations = [
    (h, i, r, c, a1, a2, a3, a4, a5, g1, g2, g3, g4)
    for h in health_statuses
    for i in infection_rates
    for r in regulation_strictness
    for c in compliance_by_others
    for a1 in alpha_values
    for a2 in alpha_values
    for a3 in alpha_values
    for a4 in alpha_values
    for a5 in alpha_values
    for g1 in gamma_values
    for g2 in gamma_values
    for g3 in gamma_values
    for g4 in gamma_values
]

# Randomly sample from all combinations to reduce memory usage
sample_size = min(5000, len(all_combinations))  # Limit the sample size to 5000 combinations
sampled_combinations = random.sample(all_combinations, sample_size)

# Convert sampled combinations to DataFrame for easier manipulation
columns = ['health_status', 'infection_rate', 'regulation_strictness', 'compliance_by_others',
           'alpha_1', 'alpha_2', 'alpha_3', 'alpha_4', 'alpha_5',
           'gamma_1', 'gamma_2', 'gamma_3', 'gamma_4']
df = pd.DataFrame(sampled_combinations, columns=columns)

# Step 4: Define default strategy function for 0th-order ToM
def default_strategy(I, R, C, H):
    if H == 1:  # Healthy
        p = 0.34 * I + 0.33 * (R * (100 - C) / 100) + 0.33 * C
    elif H == 0:  # Infected
        p = 0.34 * (-I) + 0.33 * (R * (100 - C) / 100) + 0.33 * C
    elif H == 2:  # Immune
        p = 0.5 * (R * (100 - C) / 100) + 0.5 * C
    normalized_p = (p + 100) / 200  # Normalize between 0 and 1
    return normalized_p

# Step 5: Define functions for 1st and 2nd order ToM
def first_order_strategy(row, perceived_compliance_others):
    I, R, C, H = row['infection_rate'], row['regulation_strictness'], row['compliance_by_others'], row['health_status']
    alpha_1, alpha_2, alpha_3, alpha_4, alpha_5 = row['alpha_1'], row['alpha_2'], row['alpha_3'], row['alpha_4'], row['alpha_5']
    gamma_1, gamma_2, gamma_3 = row['gamma_1'], row['gamma_2'], row['gamma_3']

    # Desires
    D_H = alpha_1 * I + alpha_2 * (1 - H)
    D_E = alpha_3 * (1 - R) + alpha_4 * (1 - C)
    D_S = alpha_5 * perceived_compliance_others

    # Logistic model
    exponent = -(0.2 + 1.2 * I + 1.0 * R + 0.8 * H + 0.5 * C + gamma_1 * D_H - gamma_2 * D_E + gamma_3 * D_S)
    compliance_probability = 1 / (1 + np.exp(exponent))
    return compliance_probability

def second_order_strategy(row, perceived_compliance_others, perceived_beliefs_about_self):
    I, R, C, H = row['infection_rate'], row['regulation_strictness'], row['compliance_by_others'], row['health_status']
    alpha_1, alpha_2, alpha_3, alpha_4, alpha_5 = row['alpha_1'], row['alpha_2'], row['alpha_3'], row['alpha_4'], row['alpha_5']
    gamma_1, gamma_2, gamma_3, gamma_4 = row['gamma_1'], row['gamma_2'], row['gamma_3'], row['gamma_4']

    # Desires
    D_H = alpha_1 * I + alpha_2 * (1 - H)
    D_E = alpha_3 * (1 - R) + alpha_4 * (1 - C)
    D_S = alpha_5 * perceived_compliance_others
    D_B = gamma_4 * perceived_beliefs_about_self

    # Logistic model
    exponent = -(0.2 + 1.2 * I + 1.0 * R + 0.8 * H + 0.5 * C + gamma_1 * D_H - gamma_2 * D_E + gamma_3 * D_S + D_B)
    compliance_probability = 1 / (1 + np.exp(exponent))
    return compliance_probability

# Step 6: Calculate compliance probabilities for each ToM level
compliance_results = []

for idx, row in df.iterrows():
    # 0th-order ToM
    compliance_0th = default_strategy(row['infection_rate'], row['regulation_strictness'],
                                      row['compliance_by_others'], row['health_status'])
    compliance_results.append([*row, compliance_0th, '0th-Order'])

    # 1st-order ToM
    perceived_compliance_others = row['compliance_by_others']
    compliance_1st = first_order_strategy(row, perceived_compliance_others)
    compliance_results.append([*row, compliance_1st, '1st-Order'])

    # 2nd-order ToM
    perceived_beliefs_about_self = 0.7  # Assumed constant for simplicity
    compliance_2nd = second_order_strategy(row, perceived_compliance_others, perceived_beliefs_about_self)
    compliance_results.append([*row, compliance_2nd, '2nd-Order'])

# Convert results to DataFrame
columns += ['compliance_probability', 'ToM_level']
df_compliance = pd.DataFrame(compliance_results, columns=columns)


In [47]:
fig = px.scatter_3d(df_compliance, x='infection_rate', y='regulation_strictness', z='compliance_probability', animation_frame='ToM_level', animation_group='compliance_probability',

                 title=f'Compliance Probability vs. Environmental Variables by Theory of Mind Level for health status: {health_statuses[0]}', color='compliance_probability',
                 labels={'infection_rate': 'Infection Rate',
                         'regulation_strictness': 'Regulation Strictness',
                         'compliance_probability': 'Compliance Probability',
                         'ToM_level': 'Theory of Mind Level',
                         'health_status': 'Health Status', 'alpha_1': 'alpha_1','alpha_2': 'alpha_2','alpha_3': 'alpha_3','alpha_4': 'alpha_4','alpha_5': 'alpha_5', 'gamma_1': 'gamma_1', 'gamma_2': 'gamma_2', 'gamma_3': 'gamma_3', 'gamma_4': 'gamma_4',}, width=800, height=800, hover_data={'infection_rate','regulation_strictness','compliance_probability','ToM_level','health_status', 'alpha_1','alpha_2','alpha_3','alpha_4','alpha_5', 'gamma_1', 'gamma_2', 'gamma_3', 'gamma_4',})

# Show the plot
fig.show()